In [1]:
#  Copyright 2016 The TensorFlow Authors. All Rights Reserved.
#
#  Licensed under the Apache License, Version 2.0 (the "License");
#  you may not use this file except in compliance with the License.
#  You may obtain a copy of the License at
#
#   http://www.apache.org/licenses/LICENSE-2.0
#
#  Unless required by applicable law or agreed to in writing, software
#  distributed under the License is distributed on an "AS IS" BASIS,
#  WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
#  See the License for the specific language governing permissions and
#  limitations under the License.
"""Convolutional Neural Network Estimator for MNIST, built with tf.layers."""

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)


def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  onehot_labels = tf.one_hot(indices=tf.cast(labels, tf.int32), depth=10)
  loss = tf.losses.softmax_cross_entropy(
      onehot_labels=onehot_labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)


if __name__ == "__main__":
  tf.app.run()

Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST-data\train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data\t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_task_id': 0, '_service': None, '_master': '', '_keep_checkpoint_every_n_hours': 10000, '_save_summary_steps': 100, '_model_dir': '/tmp/mnist_convnet_model', '_log_step_count_steps': 100, '_keep_checkpoint_max': 5, '_session_config': None, '_save_checkpoints_steps': None, '_num_worker_replicas': 1, '_task_type': 'worker', '_tf_random_seed': None, '_is_chief': True, '_save_checkpoints_secs': 600, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x

INFO:tensorflow:step = 1, loss = 2.31866
INFO:tensorflow:probabilities = [[ 0.10324812  0.10336706  0.10310604  0.08895059  0.09256064  0.09813921
   0.10776605  0.10397157  0.10616417  0.09272653]
 [ 0.09680977  0.10700294  0.09725876  0.08716851  0.09784935  0.09782521
   0.09823131  0.10690402  0.10355288  0.10739722]
 [ 0.1043432   0.10063116  0.11115919  0.08742734  0.10427509  0.1019593
   0.09024896  0.1013687   0.10919449  0.0893925 ]
 [ 0.10094331  0.10411739  0.09537559  0.08219634  0.1133614   0.0939151
   0.09178279  0.10438748  0.11498259  0.09893808]
 [ 0.10516833  0.09483397  0.10164616  0.0853185   0.10674638  0.09692299
   0.09906816  0.10637359  0.11217695  0.09174487]
 [ 0.11556934  0.10186794  0.09210809  0.08192429  0.09661717  0.09679298
   0.10358778  0.10584178  0.10536017  0.10033049]
 [ 0.09500369  0.10687181  0.09962957  0.09157964  0.10772327  0.0959923
   0.09447557  0.09821822  0.1088879   0.10161816]
 [ 0.10448907  0.10629221  0.09868795  0.10059559  0.10

INFO:tensorflow:global_step/sec: 2.619
INFO:tensorflow:probabilities = [[ 0.11403146  0.09926755  0.10070161  0.08950367  0.10776407  0.08844912
   0.09233934  0.1003096   0.10959899  0.09803465]
 [ 0.10419159  0.10998376  0.10274853  0.08718734  0.09712344  0.09576932
   0.09561477  0.10188707  0.10502737  0.10046685]
 [ 0.09524006  0.09919486  0.10456097  0.08315813  0.10199521  0.10013048
   0.10100377  0.10144146  0.11059166  0.10268343]
 [ 0.09708687  0.11487599  0.10061528  0.08712147  0.0956913   0.09496407
   0.09503208  0.10874536  0.10419616  0.10167148]
 [ 0.0994884   0.09473739  0.10316085  0.09602313  0.10931248  0.09265828
   0.09776918  0.09993053  0.1115467   0.09537317]
 [ 0.1007326   0.11343939  0.10751584  0.09373231  0.09392685  0.10367902
   0.08423536  0.10872579  0.10312099  0.09089186]
 [ 0.11596361  0.1001158   0.09702278  0.09200377  0.0971556   0.09930375
   0.09521668  0.09551222  0.12117416  0.08653163]
 [ 0.09922121  0.097295    0.09909121  0.08950461  0.1

INFO:tensorflow:step = 101, loss = 2.29768 (38.207 sec)
INFO:tensorflow:probabilities = [[ 0.09952863  0.10296682  0.08985507  0.08118149  0.10715549  0.09488309
   0.09632631  0.11149035  0.10791615  0.10869662]
 [ 0.10089411  0.10087677  0.10502361  0.08652464  0.09476334  0.09902363
   0.10691056  0.09735827  0.10289483  0.1057303 ]
 [ 0.1001683   0.10162173  0.09385589  0.08686572  0.10405052  0.09526293
   0.09503219  0.1080817   0.11134853  0.10371248]
 [ 0.09907302  0.11143873  0.09514439  0.08868945  0.08653613  0.10674877
   0.09308064  0.11191352  0.10748857  0.09988672]
 [ 0.10466804  0.09938059  0.10521408  0.08523034  0.09175816  0.0957339
   0.10885628  0.09672669  0.11301643  0.09941541]
 [ 0.09828254  0.09331217  0.10306579  0.08326779  0.1067037   0.09812883
   0.1010764   0.1021603   0.10321813  0.11078434]
 [ 0.10619666  0.09904712  0.09325832  0.0950249   0.10317773  0.10692277
   0.10065228  0.10157143  0.09852228  0.09562645]
 [ 0.10439307  0.09724336  0.09382635 

INFO:tensorflow:global_step/sec: 2.67685
INFO:tensorflow:probabilities = [[ 0.1022286   0.10290018  0.10225301  0.09049208  0.09986236  0.09600638
   0.10388825  0.10242685  0.10015583  0.09978645]
 [ 0.10278337  0.10939222  0.09604165  0.08646194  0.09611312  0.08714421
   0.10453314  0.10266484  0.12050959  0.09435589]
 [ 0.10971176  0.10714662  0.11129107  0.08578774  0.10295291  0.08787699
   0.09310815  0.10025265  0.11167951  0.09019262]
 [ 0.09825602  0.09938864  0.10362002  0.08947373  0.10370775  0.09514783
   0.10169656  0.10384734  0.10965822  0.09520386]
 [ 0.10069718  0.09493183  0.09440403  0.10010717  0.10863058  0.09745202
   0.09637009  0.10417426  0.11162507  0.09160767]
 [ 0.1184836   0.10175591  0.08881493  0.08026572  0.11319858  0.092242
   0.09658077  0.09884948  0.11516959  0.09463947]
 [ 0.0974906   0.09734512  0.10762609  0.08631208  0.08704796  0.08790323
   0.10425916  0.10147166  0.11082963  0.11971454]
 [ 0.10106349  0.10045759  0.10332713  0.11269429  0.1

...

INFO:tensorflow:global_step/sec: 2.70723
INFO:tensorflow:probabilities = [[ 0.00004382  0.00004366  0.00015907  0.99483442  0.00000501  0.00486474
   0.00000669  0.00001653  0.00001158  0.00001455]
 [ 0.9999578   0.00000007  0.00002311  0.00000616  0.00000046  0.0000025
   0.00000487  0.00000059  0.0000009   0.00000335]
 [ 0.00000057  0.00071344  0.00002429  0.99739754  0.00002497  0.00049367
   0.00000027  0.00008041  0.00082697  0.00043803]
 [ 0.99447376  0.00000084  0.00046958  0.00001366  0.00000035  0.00000421
   0.00006826  0.00015428  0.00000123  0.00481382]
 [ 0.00000082  0.00004197  0.0002326   0.00465014  0.00001309  0.00112726
   0.00000874  0.00000011  0.99390477  0.00002046]
 [ 0.00954169  0.00041309  0.00165561  0.00101424  0.00152852  0.97404218
   0.00387581  0.00255988  0.00142611  0.00394291]
 [ 0.00943525  0.00021909  0.0414046   0.00048863  0.00429548  0.00249214
   0.00077736  0.0060928   0.84020007  0.09459454]
 [ 0.00015737  0.0011899   0.12735274  0.03697021  0.

INFO:tensorflow:step = 19901, loss = 0.144439 (36.945 sec)
INFO:tensorflow:probabilities = [[ 0.00032039  0.00341925  0.00026258  0.00142044  0.00080919  0.99035913
   0.00017949  0.00028558  0.0023839   0.00056015]
 [ 0.00010164  0.00000034  0.00040686  0.00000111  0.00038232  0.00001675
   0.99908686  0.00000006  0.00000358  0.00000044]
 [ 0.00003193  0.99312747  0.00077655  0.00213067  0.00019708  0.00022158
   0.00005517  0.00105671  0.00195526  0.00044753]
 [ 0.00000044  0.00000268  0.00199173  0.00203299  0.00000581  0.00000026
   0.00000001  0.99550736  0.00002167  0.00043701]
 [ 0.00000001  0.00000013  0.00000024  0.00000052  0.99994516  0.00000009
   0.00000021  0.00000032  0.00000011  0.00005301]
 [ 0.00016915  0.12383807  0.000108    0.00296132  0.10508719  0.02774064
   0.00099881  0.01445286  0.01315132  0.71149266]
 [ 0.00000022  0.00000019  0.00013177  0.00000199  0.00017391  0.00000145
   0.99968922  0.          0.00000128  0.00000003]
 [ 0.00063274  0.00007338  0.02511

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:Loss for final step: 0.125294.
INFO:tensorflow:Starting evaluation at 2017-11-19-20:02:13
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model\model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2017-11-19-20:02:26
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9702, global_step = 20000, loss = 0.101672
{'accuracy': 0.9702, 'global_step': 20000, 'loss': 0.10167228}


SystemExit: 

C:\Users\salee\Anaconda3\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:2870: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
